In [1]:
import os, sys, json
from preprocess.process_cypher import get_schema_from_json

### Test dataset builder --> done!

In [2]:

schema = get_schema_from_json(os.getcwd() + '/data/text2cypher/schema.json')

In [3]:
schema

{'flight_company': {'db_id': 'flight_company',
  'tag_names_original': ['airport', 'operate_company', 'flight'],
  'tag_names': [':`flight_company.airport`',
   ':`flight_company.operate_company`',
   ':`flight_company.flight`'],
  'property_names': [[-1, '*'],
   [0, 'name'],
   [0, 'IATA'],
   [0, 'Country'],
   [0, 'ICAO'],
   [0, 'id'],
   [0, 'City'],
   [1, 'name'],
   [1, 'id'],
   [1, 'Type'],
   [1, 'Principal_activities'],
   [1, 'Incorporated_in'],
   [1, 'Group_Equity_Shareholding'],
   [2, 'id'],
   [2, 'Pilot'],
   [2, 'airport_id'],
   [2, 'company_id'],
   [2, 'Vehicle_Flight_number'],
   [2, 'Velocity'],
   [2, 'Date'],
   [2, 'Altitude']],
  'property_types': ['String',
   'String',
   'String',
   'String',
   'Long',
   'String',
   'String',
   'Long',
   'String',
   'String',
   'String',
   'Double',
   'Long',
   'String',
   'Long',
   'Long',
   'String',
   'Double',
   'String',
   'Double'],
  'airport': {'name': ['Baltimore-Washington Airport',
    'Akure

In [4]:

schema_cache = {}
for split in ['train.json', 'dev.json']:
    dev_fpath = os.getcwd() + '/data/text2cypher/'+ split
    with open(dev_fpath, 'r', encoding="utf-8") as f:
        data = json.load(f)
        print(len(data))
        for idx, sample in enumerate(data):
            db_id = sample["db_id"]
            if db_id == 'department_management':
                for item in schema:
                    if db_id not in schema_cache:
                        schema_cache[db_id] = schema[db_id]
                schema = schema_cache[db_id]
                print(db_id)
                print(sample)
                print(schema)
                
                test = {
                "db_id": db_id,
                "query": sample["query"],
                "question": sample["question"],
                "answers": sample["answers"],
                "db_tag_names": schema['tag_names'], 
                "db_property_names": 
                    [
                        {
                            "tag_id": tag_id, "property_name": property_name
                        }
                        for tag_id, property_name in schema['property_names']
                    ],
                "db_property_types": schema['property_types']
                }
            print(test)

3175
department_management
{'question': 'How many heads of the departments are older than 56 ?', 'query': 'MATCH (head:`department_management.head`)\nWHERE head.age > 56\nRETURN count(*)', 'db_id': 'department_management', 'answers': [[5]]}
{'db_id': 'department_management', 'tag_names_original': ['department', 'head', 'management'], 'tag_names': [':`department_management.department`', ':`department_management.head`', ':`department_management.management`'], 'property_names': [[-1, '*'], [0, 'Name'], [0, 'Creation'], [0, 'Department_ID'], [0, 'Ranking'], [0, 'Budget_in_Billions'], [0, 'Num_Employees'], [1, 'name'], [1, 'born_state'], [1, 'age'], [1, 'head_ID'], [2, 'temporary_acting']], 'property_types': ['String', 'String', 'Long', 'Long', 'Double', 'Double', 'String', 'String', 'Double', 'Long', 'String'], 'department': {'Name': ['Treasury', 'Defense', 'Justice', 'Interior', 'Health and Human Services', 'Agriculture', 'Transportation', 'Energy', 'Veterans Affairs', 'Education', 'Comme

In [5]:
from seq2seq_construction.text2cypher_dataset_builder import Text2Cypher
data_builder = Text2Cypher()

/usr/local/lib/python3.8/dist-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/usr/lib/python3/dist-packages/requests/__init__.py:89: RequestsDependencyWarning: urllib3 (1.26.12) or chardet (3.0.4) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({}) doesn't match a supported "


In [6]:
for split in ['train.json', 'dev.json']:
    dev_fpath = os.getcwd() + '/data/text2cypher/'+ split
    data_builder._generate_examples(dev_fpath, os.getcwd() + '/data/text2cypher/schema.json')

In [7]:
data_builder._info()

DatasetInfo(description='Spider is a large-scale complex and cross-domain semantic parsing and text-toSQL dataset annotated by 11 college students.\nWe use a dataset transformed from a subset of Spider to train our Text-to-Cypher semantic parsing.\n', citation='@article{yu2018spider,\n  title={Spider: A large-scale human-labeled dataset for complex and cross-domain semantic parsing and text-to-sql task},\n  author={Yu, Tao and Zhang, Rui and Yang, Kai and Yasunaga, Michihiro and Wang, Dongxu and Li, Zifan and Ma, James and Li, Irene and Yao, Qingning and Roman, Shanelle and others},\n  journal={arXiv preprint arXiv:1809.08887},\n  year={2018}\n}\n\n@article{raffel2020exploring,\n  title={Exploring the limits of transfer learning with a unified text-to-text transformer},\n  author={Raffel, Colin and Shazeer, Noam and Roberts, Adam and Lee, Katherine and Narang, Sharan and Matena, Michael and Zhou, Yanqi and Li, Wei and Liu, Peter J},\n  journal={The Journal of Machine Learning Research}

### Test DB content encoding --> done!

In [8]:
import sqlite3
db_path = '/home/22842219/Desktop/projects_data/spider/database/department_management/department_management.sqlite'
table_name = 'head'
column_name = 'born_state'
question = 'What are the names of the heads who are born outside the California state?'

In [9]:
# picklist saves all the 'name' column values
# test column values picklist
def get_column_picklist(table_name: str, column_name: str, db_path: str) -> list:
    fetch_sql = "SELECT DISTINCT `{}` FROM `{}`".format(column_name, table_name)
    try:
        conn = sqlite3.connect(db_path)
        conn.text_factory = bytes
        c = conn.cursor()
        c.execute(fetch_sql)
        picklist = set()
        for x in c.fetchall():
            if isinstance(x[0], str):
                picklist.add(x[0].encode("utf-8"))
            elif isinstance(x[0], bytes):
                try:
                    picklist.add(x[0].decode("utf-8"))
                except UnicodeDecodeError:
                    picklist.add(x[0].decode("latin-1"))
            else:
                picklist.add(x[0])
        picklist = list(picklist)
    finally:
        conn.close()
    return picklist

picklist = get_column_picklist(table_name, column_name, db_path)
print(picklist)

['Delaware', 'California', 'Florida', 'Alabama', 'Connecticut']


In [10]:
from seq2seq_construction.bridge_content_encoder import is_stopword, is_number, is_common_db_term, get_effective_match_source, prefix_match, is_commonword, split

In [11]:
import difflib
from typing import List, Optional, Tuple
from rapidfuzz import fuzz
import sqlite3
import functools

In [12]:
def get_matched_entries(
    s: str, field_values: List[str], m_theta: float = 0.85, s_theta: float = 0.85
) -> Optional[List[Tuple[str, Tuple[str, str, float, float, int]]]]:
    if not field_values:
        return None

    if isinstance(s, str):
        n_grams = split(s)
    else:
        n_grams = s

    matched = dict()
    print(f'n_grams: {n_grams}')
    for id, field_value in enumerate(field_values):
        if not isinstance(field_value, str):
            continue
        fv_tokens = split(field_value)   
        sm = difflib.SequenceMatcher(None, n_grams, fv_tokens)
        match = sm.find_longest_match(0, len(n_grams), 0, len(fv_tokens))
        if match.size > 0:
            source_match = get_effective_match_source(
                n_grams, match.a, match.a + match.size
            )

            if source_match and source_match.size > 1:

                print(f'{id}, field_value: {field_value}, fv_tokens: {fv_tokens}, n_grams: {n_grams}')
                print(f'sm: {sm}, match: {match}')
                print(f'match_start: {match.a}, match_end:{match.size + match.a}')
                print(n_grams[match.a])
                print(f'source_match: {source_match}')
                print(field_value[match.b : match.b + match.size])

                match_str = field_value[match.b : match.b + match.size]
                source_match_str = s[
                    source_match.start : source_match.start + source_match.size
                ]
                c_match_str = match_str.lower().strip()
                c_source_match_str = source_match_str.lower().strip()
                c_field_value = field_value.lower().strip()
                if (
                    c_match_str
                    and not is_number(c_match_str)
                    and not is_common_db_term(c_match_str)
                ):
                    if (
                        is_stopword(c_match_str)
                        or is_stopword(c_source_match_str)
                        or is_stopword(c_field_value)
                    ):
                        continue
                    if c_source_match_str.endswith(c_match_str + "'s"):
                        match_score = 1.0
                    else:
                        if prefix_match(c_field_value, c_source_match_str):
                            match_score = (
                                fuzz.ratio(c_field_value, c_source_match_str) / 100
                            )
                        else:
                            match_score = 0
                    if (
                        is_commonword(c_match_str)
                        or is_commonword(c_source_match_str)
                        or is_commonword(c_field_value)
                    ) and match_score < 1:
                        continue
                    s_match_score = match_score
                    if match_score >= m_theta and s_match_score >= s_theta:
                        if field_value.isupper() and match_score * s_match_score < 1:
                            continue
                        matched[match_str] = (
                            field_value,
                            source_match_str,
                            match_score,
                            s_match_score,
                            match.size,
                        )
    # for understanding process
    for match_str, value in matched.items():
        print(f'match_str: {match_str}')
        print(f'(field_value, source_match_str, match_score, s_match_score, match.size):  {value}')
    # for understanding process 

    if not matched:
        return None
    else:
        return sorted(
            matched.items(),
            key=lambda x: (1e16 * x[1][2] + 1e8 * x[1][3] + x[1][4]),
            reverse=True,
        )



In [13]:
matches_entries = get_matched_entries(question, picklist, m_theta = 0.85, s_theta = 0.85)
print(matches_entries)

n_grams: ['w', 'h', 'a', 't', ' ', 'a', 'r', 'e', ' ', 't', 'h', 'e', ' ', 'n', 'a', 'm', 'e', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'h', 'e', 'a', 'd', 's', ' ', 'w', 'h', 'o', ' ', 'a', 'r', 'e', ' ', 'b', 'o', 'r', 'n', ' ', 'o', 'u', 't', 's', 'i', 'd', 'e', ' ', 't', 'h', 'e', ' ', 'c', 'a', 'l', 'i', 'f', 'o', 'r', 'n', 'i', 'a', ' ', 's', 't', 'a', 't', 'e', '?']
0, field_value: Delaware, fv_tokens: ['d', 'e', 'l', 'a', 'w', 'a', 'r', 'e'], n_grams: ['w', 'h', 'a', 't', ' ', 'a', 'r', 'e', ' ', 't', 'h', 'e', ' ', 'n', 'a', 'm', 'e', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'h', 'e', 'a', 'd', 's', ' ', 'w', 'h', 'o', ' ', 'a', 'r', 'e', ' ', 'b', 'o', 'r', 'n', ' ', 'o', 'u', 't', 's', 'i', 'd', 'e', ' ', 't', 'h', 'e', ' ', 'c', 'a', 'l', 'i', 'f', 'o', 'r', 'n', 'i', 'a', ' ', 's', 't', 'a', 't', 'e', '?']
sm: <difflib.SequenceMatcher object at 0x7f016d1338b0>, match: Match(a=5, b=5, size=3)
match_start: 5, match_end:8
a
source_match: <seq2seq_construction.bridge_c

In [14]:
def get_database_matches(
    question: str,
    table_name: str,
    column_name: str,
    db_path: str,
    top_k_matches: int = 2,
    match_threshold: float = 0.85,
) -> List[str]:
    picklist = get_column_picklist(
        table_name=table_name, column_name=column_name, db_path=db_path
    )
    print(f'picklist: {picklist}, question: {type(question)}, {question}')
    matches = []
    if picklist and isinstance(picklist[0], str):
        matched_entries = get_matched_entries(
            s=question,
            field_values=picklist,
            m_theta=match_threshold,
            s_theta=match_threshold,
        )
        if matched_entries:
            num_values_inserted = 0
            for _match_str, (
                field_value,
                _s_match_str,
                match_score,
                s_match_score,
                _match_size,
            ) in matched_entries:
                if "name" in column_name and match_score * s_match_score < 1:
                    continue
                if table_name != "sqlite_sequence":  # Spider database artifact
                    matches.append(field_value)
                    num_values_inserted += 1
                    if num_values_inserted >= top_k_matches:
                        break
    return matches

In [15]:
matches = get_database_matches(question, table_name, column_name, db_path)
print(matches)

picklist: ['Delaware', 'California', 'Florida', 'Alabama', 'Connecticut'], question: <class 'str'>, What are the names of the heads who are born outside the California state?
n_grams: ['w', 'h', 'a', 't', ' ', 'a', 'r', 'e', ' ', 't', 'h', 'e', ' ', 'n', 'a', 'm', 'e', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'h', 'e', 'a', 'd', 's', ' ', 'w', 'h', 'o', ' ', 'a', 'r', 'e', ' ', 'b', 'o', 'r', 'n', ' ', 'o', 'u', 't', 's', 'i', 'd', 'e', ' ', 't', 'h', 'e', ' ', 'c', 'a', 'l', 'i', 'f', 'o', 'r', 'n', 'i', 'a', ' ', 's', 't', 'a', 't', 'e', '?']
0, field_value: Delaware, fv_tokens: ['d', 'e', 'l', 'a', 'w', 'a', 'r', 'e'], n_grams: ['w', 'h', 'a', 't', ' ', 'a', 'r', 'e', ' ', 't', 'h', 'e', ' ', 'n', 'a', 'm', 'e', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'h', 'e', 'a', 'd', 's', ' ', 'w', 'h', 'o', ' ', 'a', 'r', 'e', ' ', 'b', 'o', 'r', 'n', ' ', 'o', 'u', 't', 's', 'i', 'd', 'e', ' ', 't', 'h', 'e', ' ', 'c', 'a', 'l', 'i', 'f', 'o', 'r', 'n', 'i', 'a', ' ', 's', 't', 'a', '

In [38]:
from seq2seq_construction.bridge_content_encoder import get_database_matches, get_property_picklist
# test ours DB content encoding
import codecs, json
schema_path = '/home/22842219/Desktop/phd/SemanticParser4Graph/semantic_parser/data/text2cypher/schema.json'
db_id = 'department_management'
tag_name = ":`department_management.head`"
property_name = 'born_state'
question = 'What are the names of the heads who are born outside the California state?'
print(f'question: {question}')
print(f'tag_name: {tag_name}')
print(f'property_name: {property_name}')


question: What are the names of the heads who are born outside the California state?
tag_name: :`department_management.head`
property_name: born_state


In [41]:
def get_property_picklist(db_id: str, tag_name: str, property_name: str, schema_path: str) -> list:
    with codecs.open(schema_path, 'r') as f:
        schema = json.load(f)
        every_schema=schema[db_id]
        if tag_name.startswith(":`"):
            tag_name = tag_name.strip(":").strip("`").split(".")[1]
        property_name_value_pairs = every_schema[tag_name]
        print(every_schema)
        return property_name_value_pairs[property_name]



In [43]:
tag_name

':`department_management.head`'

In [42]:
text2cypher_picklist = get_property_picklist(db_id, tag_name, property_name, schema_path)
print(f'text2cypher_picklist: {text2cypher_picklist}')

{'db_id': 'department_management', 'tag_names_original': ['department', 'head', 'management'], 'tag_names': [':`department_management.department`', ':`department_management.head`', ':`department_management.management`'], 'property_names': [[-1, '*'], [0, 'Name'], [0, 'Creation'], [0, 'Department_ID'], [0, 'Ranking'], [0, 'Budget_in_Billions'], [0, 'Num_Employees'], [1, 'name'], [1, 'born_state'], [1, 'age'], [1, 'head_ID'], [2, 'temporary_acting']], 'property_types': ['String', 'String', 'Long', 'Long', 'Double', 'Double', 'String', 'String', 'Double', 'Long', 'String'], 'department': {'Name': ['Defense', 'Interior', 'Agriculture', 'Transportation', 'Labor', 'State', 'Commerce', 'Health and Human Services', 'Energy', 'Homeland Security', 'Education', 'Veterans Affairs', 'Treasury', 'Housing and Urban Development', 'Justice'], 'Creation': ['1947', '1965', '1849', '1789', '1913', '1870', '1977', '1903', '1889', '2002', '1979', '1989', '1953', '1966'], 'Department_ID': [1, 2, 3, 4, 5, 6, 

In [19]:
tag_name

':`department_management.head`'

In [20]:
matches = get_database_matches(db_id, question, tag_name, property_name, schema_path)
print(matches)

picklist: ['Connecticut', 'Delaware', 'California', 'Florida', 'Alabama'], question: <class 'str'>, What are the names of the heads who are born outside the California state?
n_grams: ['w', 'h', 'a', 't', ' ', 'a', 'r', 'e', ' ', 't', 'h', 'e', ' ', 'n', 'a', 'm', 'e', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'h', 'e', 'a', 'd', 's', ' ', 'w', 'h', 'o', ' ', 'a', 'r', 'e', ' ', 'b', 'o', 'r', 'n', ' ', 'o', 'u', 't', 's', 'i', 'd', 'e', ' ', 't', 'h', 'e', ' ', 'c', 'a', 'l', 'i', 'f', 'o', 'r', 'n', 'i', 'a', ' ', 's', 't', 'a', 't', 'e', '?']
fv_tokens:
fv_tokens:
fv_tokens:
fv_tokens:
fv_tokens:
['California']


### Test input serialization

In [21]:

import os, torch
from tqdm import tqdm
from copy import deepcopy
import datasets




In [22]:
### test text2sql
%cd '/home/22842219/Desktop/openSource/UnifiedSKGG-subSpider'
os.getcwd()
loader_path = 'tasks/spider.py'
data_store_path ='data'
cache_root = os.getcwd() + '/out/cache'

/home/22842219/Desktop/openSource/UnifiedSKGG-subSpider


In [23]:

raw_datasets_split: datasets.DatasetDict = datasets.load_dataset(path=loader_path, cache_dir=data_store_path)


Reusing dataset spider (data/spider/spider/1.0.0/8cb9bd1805fb49e5d5c8026f611e26df74707b5b79743abe53b5a8965aee35b9)
100%|██████████| 2/2 [00:00<00:00, 309.84it/s]


In [24]:
raw_datasets_split.data

{'train': MemoryMappedTable
 query: string
 question: string
 db_id: string
 db_path: string
 db_table_names: list<item: string>
   child 0, item: string
 db_column_names: struct<table_id: list<item: int32>, column_name: list<item: string>>
   child 0, table_id: list<item: int32>
       child 0, item: int32
   child 1, column_name: list<item: string>
       child 0, item: string
 db_column_types: list<item: string>
   child 0, item: string
 db_primary_keys: struct<column_id: list<item: int32>>
   child 0, column_id: list<item: int32>
       child 0, item: int32
 db_foreign_keys: struct<column_id: list<item: int32>, other_column_id: list<item: int32>>
   child 0, column_id: list<item: int32>
       child 0, item: int32
   child 1, other_column_id: list<item: int32>
       child 0, item: int32
 ----
 query: [["SELECT count(*) FROM head WHERE age  >  56","SELECT name ,  born_state ,  age FROM head ORDER BY age","SELECT creation ,  name ,  budget_in_billions FROM department","SELECT max(bu

In [25]:
raw_datasets_split.__getitem__

<bound method DatasetDict.__getitem__ of DatasetDict({
    train: Dataset({
        features: ['query', 'question', 'db_id', 'db_path', 'db_table_names', 'db_column_names', 'db_column_types', 'db_primary_keys', 'db_foreign_keys'],
        num_rows: 4730
    })
    validation: Dataset({
        features: ['query', 'question', 'db_id', 'db_path', 'db_table_names', 'db_column_names', 'db_column_types', 'db_primary_keys', 'db_foreign_keys'],
        num_rows: 705
    })
})>

In [26]:
raw_datasets_split

DatasetDict({
    train: Dataset({
        features: ['query', 'question', 'db_id', 'db_path', 'db_table_names', 'db_column_names', 'db_column_types', 'db_primary_keys', 'db_foreign_keys'],
        num_rows: 4730
    })
    validation: Dataset({
        features: ['query', 'question', 'db_id', 'db_path', 'db_table_names', 'db_column_names', 'db_column_types', 'db_primary_keys', 'db_foreign_keys'],
        num_rows: 705
    })
})

In [27]:
# text2cypher data serialization

import os, torch
from tqdm import tqdm
from copy import deepcopy
import datasets


%cd '/home/22842219/Desktop/phd/SemanticParser4Graph/semantic_parser'
os.getcwd()
loader_path = 'seq2seq_construction/text2cypher_dataset_builder.py'
data_store_path ='data'
cache_root = os.getcwd() + '/out/cache'

/home/22842219/Desktop/phd/SemanticParser4Graph/semantic_parser


In [28]:

raw_datasets_split: datasets.DatasetDict = datasets.load_dataset(path=loader_path, cache_dir=data_store_path)


Dataset text2_cypher downloaded and prepared to data/text2_cypher/text2cypher/1.0.0/9a357b853717b5477de0f3366bc46fa3acccb14451d367061841b05a3909f446. Subsequent calls will reuse this data.


100%|██████████| 2/2 [00:00<00:00, 439.29it/s]


In [29]:
raw_datasets_split


DatasetDict({
    train: Dataset({
        features: ['query', 'question', 'schema_path', 'db_id', 'db_tag_names', 'db_property_names', 'db_property_types'],
        num_rows: 3175
    })
    validation: Dataset({
        features: ['query', 'question', 'schema_path', 'db_id', 'db_tag_names', 'db_property_names', 'db_property_types'],
        num_rows: 491
    })
})

### Test evaluation metrics

In [1]:
import os, sys
import json
import argparse

from py2neo import Graph
import configparser
config = configparser.ConfigParser()
config.read('/home/22842219/Desktop/phd/SemanticParser4Graph/application/config.ini')
filenames = config["FILENAMES"]

neo4j_uri = filenames['neo4j_uri']
neo4j_user = filenames['neo4j_user']
neo4j_password = filenames['neo4j_password']
graph = Graph(neo4j_uri, auth = (neo4j_user, neo4j_password))



In [3]:
from preprocess.process_cypher import Schema, get_schema_from_json
from metrics.text2cypher.evaluator import evaluate
gold_path = '/home/22842219/Desktop/phd/SemanticParser4Graph/semantic_parser/metrics/text2cypher/gold_testing_example'
predict_path = '/home/22842219/Desktop/phd/SemanticParser4Graph/semantic_parser/metrics/text2cypher/predict_testing_example'
evaluate(gold_path, predict_path, graph, 'all')

1
count                1                    
=====================   EXECUTION ACCURACY     =====================
execution            0.000                


{'per_item': [{'predicted': ['"MATCH (T1:`concert_singer.concert`)-[]-(T2:`concert_singer.stadium`)\\nWITH T2.Name AS Name, count(T1.Stadium_ID) AS count\\nRETURN Name,count"'],
   'gold': ['"MATCH (T1:`concert_singer.concert`)-[]-(T2:`concert_singer.stadium`)\\nWITH T2.Name AS Name, count(T1.Stadium_ID) AS count\\nRETURN Name,count"'],
   'syntactic_error': True}],
 'total_scores': {'count': 1, 'exec': 0.0}}

In [1]:
# test two words similarity using glove
!pip install gensim

     |████████████████████████████████| 26.5 MB 27.8 MB/s eta 0:00:01    |██▍                             | 1.9 MB 27.8 MB/s eta 0:00:01
